# Do I want this undulator?

This notebooks shows how to estimate the applicability of a set of undulator params (length, period length, K, etc) to your beamline needs.
* First we compute undulator fundamental frequencies analytically and using XRT for a selected deflection value K.
* Then we compute the full undulator intensity spectrum for a deflection parameter range
* And at last we select optimal harmonic and K for a set of photon energies we intend to use, and calculate source size and divergence for each one.

## Imports

In [1]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.io as pio
import plotly.figure_factory as ff
pio.renderers.default = 'iframe'

from scipy.spatial import Delaunay
import matplotlib
from matplotlib import pyplot as plt

import xrt.backends.raycing.sources as rs
import params.sources as ps
from scipy.signal import find_peaks
from scipy.interpolate import griddata
from scipy.interpolate import UnivariateSpline

import adaptive
adaptive.notebook_extension()

/nix/store/br42xxsq58x87i1w4lh2vnz807fw84b3-python3.12-pytools-2025.1.1/lib/python3.12/site-packages/pytools/persistent_dict.py:52: RecommendedHashNotFoundWarning:

Unable to import recommended hash 'siphash24.siphash13', falling back to 'hashlib.sha256'. Run 'python3 -m pip install siphash24' to install the recommended hash.



## Computing undulator spectrum
Here we compare the fundamental frequencies computation formula with XRT undulator modelling code

Formulas from Willmott:
$$
n \lambda _n [\mathrm{AA}]= \frac{13.056 \cdot \lambda _u [\mathrm{cm}]}{\mathcal{E} ^2 [\mathrm{GeV}]} \cdot \left(  1 + \frac{K^2}{2}\right)
$$
$$
E [\textrm{eV}] = \frac{12398}{\lambda [\textrm{AA}]}
$$

In [2]:
# setting up computation mesh:
# Intensities will be computed over a 3D mesh grid of 
# energies, theta, and psi 
energy = np.linspace(1.0e3, 21.0e3, 4001)
theta = np.linspace(-1, 1, 51) * 30e-6
psi = np.linspace(-1, 1, 51) * 30e-6

# setting up undulator params
# computational limits, 
# storage ring params (energy, current, etc),
# insertion device params (deflection K, period, length, etc)
und_kwargs = dict(
    xPrimeMax=theta[-1] * 1e3,
    zPrimeMax=psi[-1] * 1e3,
    **ps.ring_kwargs,
    **ps.undulator_1_1_kwargs,
    targetOpenCL="CPU",
    distE="BW",
)

# computing intensities on 3D mesh grid
source = rs.Undulator(**und_kwargs)
I0, l1, l2, l3 = source.intensities_on_mesh(energy, theta, psi)

# integrating over angles to get total flux 
dtheta, dpsi = theta[1] - theta[0], psi[1] - psi[0]
flux = I0.sum(axis=(1, 2)) * dtheta * dpsi

# plotting
fig = go.Figure()
fig.add_trace(go.Line(x=energy, y=flux, name="XRT"))
for n in range(1, 11):
    fig.add_vline(x=n * 123980. / (13.056 * ps.undulator_1_1_kwargs['period'] * (1 + 0.5 * ps.undulator_1_1_kwargs['K']**2) / ps.ring_kwargs['eE']**2))
fig.show()

peaks, _ = find_peaks(flux,prominence=1e14)
harmonics = list(energy[peaks])

OpenCL: bulding undulator.cl ...
OpenCL: found 1 CPU
OpenCL: found 1 GPU
OpenCL: found none other accelerator
OpenCL for undulator.cl: Autoselected device 0: 12th Gen Intel(R) Core(TM) i7-12800HX
precisionOpenCL = float64


/nix/store/wi0gs2lg75vbsz87x8ynaaalmkhxj1mw-python3.12-pyopencl-2025.1/lib/python3.12/site-packages/pyopencl/cache.py:496: CompilerWarning:

Built kernel retrieved from cache. Original from-source build had warnings:
Build on <pyopencl.Device '12th Gen Intel(R) Core(TM) i7-12800HX' on 'Intel(R) OpenCL' at 0x10d59188> succeeded, but said:

Compilation started
Compilation done
Linking started
Linking done
Device build started
Device build done
Kernel <undulator> was successfully vectorized (8)
Kernel <undulator_taper> was successfully vectorized (8)
Kernel <undulator_nf> was successfully vectorized (8)
Kernel <undulator_full> was successfully vectorized (8)
Kernel <undulator_nf_full> was successfully vectorized (8)
Kernel <get_trajectory_filament> was successfully vectorized (8)
Kernel <custom_field_filament> was successfully vectorized (8)
Kernel <get_trajectory> was successfully vectorized (8)
Kernel <custom_field> was successfully vectorized (8)
Done.

/nix/store/wi0gs2lg75vbsz87x8yna

Estimating convergence
Phase 1. Exponential / rough
Phase 2. Bisection / precize. 0 steps
Done estimating convergence
Done with integration optimization, 32 points will be used in 2 intervals


/nix/store/i63lpv0lgmz4gmar81x5rxksyc2nm66f-python3.12-plotly-5.24.1/lib/python3.12/site-packages/plotly/graph_objs/_deprecations.py:378: DeprecationWarning:

plotly.graph_objs.Line is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.scatter.Line
  - plotly.graph_objs.layout.shape.Line
  - etc.




## Computing undulator $I(h\nu, K)$ plot using Adaptive + XRT
Here we use [adaptive](https://adaptive.readthedocs.io/en/latest/) library to compute the undulator spectrum vs deflection parameter K dependence. Adaptive intelligently selects points in ($h\nu$, K) space to reduce computation time and make a pretty graph.

### This cell defines the computation, setting up `adaptive.Learner2D` object

In [3]:
energy = np.linspace(1.0e3, 21.0e3, 4001)
theta = np.linspace(-1, 1, 51) * 30e-6
psi = np.linspace(-1, 1, 51) * 30e-6
dtheta, dpsi = theta[1] - theta[0], psi[1] - psi[0]

und_kwargs = dict(
    xPrimeMax=theta[-1] * 1e3,
    zPrimeMax=psi[-1] * 1e3,
    **ps.ring_kwargs,
    **ps.undulator_1_1_kwargs,
    targetOpenCL="CPU",
    distE="BW",
)

source = rs.Undulator(**und_kwargs)

def log_intensity(arg):
    k, en = arg
    source.K = k
    I0, l1, l2, l3 = source.intensities_on_mesh([en], theta, psi)
    return np.log((I0.sum(axis=(1, 2)) * dtheta * dpsi)[0])

ln = adaptive.Learner2D(log_intensity, bounds=[(0.5, 1.8), (1e3, 20e3)])

OpenCL: bulding undulator.cl ...
OpenCL: found 1 CPU
OpenCL: found 1 GPU
OpenCL: found none other accelerator
OpenCL for undulator.cl: Autoselected device 0: 12th Gen Intel(R) Core(TM) i7-12800HX
precisionOpenCL = float64


/nix/store/wi0gs2lg75vbsz87x8ynaaalmkhxj1mw-python3.12-pyopencl-2025.1/lib/python3.12/site-packages/pyopencl/cache.py:496: CompilerWarning:

Built kernel retrieved from cache. Original from-source build had warnings:
Build on <pyopencl.Device '12th Gen Intel(R) Core(TM) i7-12800HX' on 'Intel(R) OpenCL' at 0x41e37038> succeeded, but said:

Compilation started
Compilation done
Linking started
Linking done
Device build started
Device build done
Kernel <undulator> was successfully vectorized (8)
Kernel <undulator_taper> was successfully vectorized (8)
Kernel <undulator_nf> was successfully vectorized (8)
Kernel <undulator_full> was successfully vectorized (8)
Kernel <undulator_nf_full> was successfully vectorized (8)
Kernel <get_trajectory_filament> was successfully vectorized (8)
Kernel <custom_field_filament> was successfully vectorized (8)
Kernel <get_trajectory> was successfully vectorized (8)
Kernel <custom_field> was successfully vectorized (8)
Done.

/nix/store/wi0gs2lg75vbsz87x8yna

### This cell starts and monitors the computation (it runs in the background and does not hold the cell)

In [5]:
runner = adaptive.Runner(ln, loss_goal=0.001)
runner.live_info()
runner.live_plot()

Button(description='cancel live-plot', layout=Layout(width='150px'), style=ButtonStyle())

:DynamicMap   []
   :Overlay
      .Image.I     :Image   [x,y]   (z)
      .EdgePaths.I :EdgePaths   [x,y]

Estimating convergenceEstimating convergenceEstimating convergenceEstimating convergenceEstimating convergence

Estimating convergenceEstimating convergenceEstimating convergenceEstimating convergenceEstimating convergenceEstimating convergencePhase 1. Exponential / roughEstimating convergence


Estimating convergence

Estimating convergence




Phase 1. Exponential / rough
Phase 1. Exponential / roughPhase 1. Exponential / roughPhase 1. Exponential / rough
Phase 1. Exponential / rough

Phase 1. Exponential / rough

Estimating convergencePhase 1. Exponential / roughPhase 1. Exponential / roughEstimating convergence
Phase 1. Exponential / rough
Phase 1. Exponential / roughPhase 1. Exponential / rough
Estimating convergenceEstimating convergence
Estimating convergenceEstimating convergencePhase 1. Exponential / roughEstimating convergence
Phase 1. Exponential / roughEstimating convergence












Phase 1. Exponential / rough
Phase 2. Bisection / precize. 0 stepsPhase 1. Exponential /

### Run this cell to stop the computation (results will be available from `Learner2D` object)

In [7]:
runner.cancel()

### Save the results to file

In [11]:
df = ln.to_dataframe(x_name="K", y_name="E", z_name="logI")
df["I"] = np.exp(df["logI"])

# save and reload data from file
df.to_csv("Undulator_1_1_flux.csv")

### Load and plot the results

In [12]:
# load data from file
df.to_csv("Undulator_1_1_flux.csv")
df = pd.read_csv("Undulator_1-1_flux.csv")

# sort the data
raw_data = df[["K", "E", "I"]].to_numpy()
ii = np.lexsort((raw_data[:, 0], raw_data[:, 1]))
raw_data = raw_data[ii]

# prep triangulation
tri_data = raw_data.copy()
tri_data[:, 0] = (tri_data[:, 0] - np.min(tri_data[:, 0])) / (np.max(tri_data[:, 0])- np.min(tri_data[:, 0]))
tri_data[:, 1] = (tri_data[:, 1] - np.min(tri_data[:, 1])) / (np.max(tri_data[:, 1])- np.min(tri_data[:, 1]))
tri = Delaunay(tri_data[:, :2])
simplices = tri.simplices.T

# plot
fig = make_subplots(rows=1, cols=2,specs=[[{"type": "scatter3d"}, {"type": "scatter3d"}]])
fig.add_trace(go.Mesh3d(
    x=raw_data[:, 0], y=raw_data[:, 1], z=raw_data[:, 2], 
    i=simplices[0], j=simplices[1], k=simplices[2],
    intensity=np.log(raw_data[:, 2]),
), row=1, col=1)

fig.add_trace(go.Scatter3d(
    x=df['K'], y=df['E'], z=df['I'], 
    mode='markers', marker=dict(color=df['logI'],size=2)), 
              row=1, col=2)
fig.show()

In [14]:
df = pd.read_csv("Undulator_1-1_flux.csv")

# sort the data
raw_data = df[["K", "E", "I"]].to_numpy()
ii = np.lexsort((raw_data[:, 0], raw_data[:, 1]))
raw_data = raw_data[ii]

# prep triangulation
tri_data = raw_data.copy()
tri_data[:, 0] = (tri_data[:, 0] - np.min(tri_data[:, 0])) / (np.max(tri_data[:, 0])- np.min(tri_data[:, 0]))
tri_data[:, 1] = (tri_data[:, 1] - np.min(tri_data[:, 1])) / (np.max(tri_data[:, 1])- np.min(tri_data[:, 1]))
tri = Delaunay(tri_data[:, :2])
simplices = tri.simplices.T

# plot
fig = make_subplots(rows=1, cols=2,specs=[[{"type": "scatter3d"}, {"type": "scatter3d"}]])
# plot as a surface
fig.add_trace(go.Mesh3d(
    x=raw_data[:, 0], y=raw_data[:, 1], z=raw_data[:, 2], 
    i=simplices[0], j=simplices[1], k=simplices[2],
    intensity=np.log(raw_data[:, 2]),
), row=1, col=1)

# plot as scatter points
fig.add_trace(go.Scatter3d(
    x=df['K'], y=df['E'], z=df['I'], 
    mode='markers', marker=dict(color=df['logI'],size=2)), 
              row=1, col=2)
fig.show()

## Computing undulator photon source size

### Using the previous plot we determined the best K and harmonic for each photon energy

In [16]:
und_configurations = [
    {"E": 8800, "K": 1.309, "harmonic": 3},  # in spectra 8850 & dx'=dz'=0.015 mrad
    {"E": 15000, "K": 1.76, "harmonic":7},   # in spectra 15100 & dx'=dz'=0.010 mrad
    {"E": 17000, "K": 1.58, "harmonic":7},
]

### For selected configurations we compute point light source approximation parameters
* Harmonic photon energy FWHM
* Source size $dx$, $dz$
* Source divergence $dx^{\prime}$, $dz^{\prime}$

In [17]:
fig = go.Figure()

theta = np.linspace(-1, 1, 51) * 30e-6
psi = np.linspace(-1, 1, 51) * 30e-6

source_params = und_configurations.copy()
for ii in range(len(source_params)):
    uconf = source_params[ii]
    ukwgs = ps.undulator_1_1_kwargs.copy()
    ukwgs["K"] = uconf["K"]
    energy = np.linspace(uconf["E"] - 500, uconf["E"] + 500, 401)

    und_kwargs = dict(
        xPrimeMax=theta[-1] * 1e3,
        zPrimeMax=psi[-1] * 1e3,
        **ps.ring_kwargs,
        **ukwgs,
        targetOpenCL="CPU",
        distE="BW",
    )

    source = rs.Undulator(**und_kwargs)
    xs, zs = source.get_SIGMA(uconf["E"])
    xps, zps = source.get_SIGMAP(uconf["E"])
    I0, l1, l2, l3 = source.intensities_on_mesh(energy, theta, psi)

    dtheta, dpsi = theta[1] - theta[0], psi[1] - psi[0]
    flux = I0.sum(axis=(1, 2)) * dtheta * dpsi

    spline = UnivariateSpline(energy, flux - np.max(flux)/2., s=0)
    r1, r2 = spline.roots()
    source_params[ii]["E FWHM"] = r2 - r1
    source_params[ii]["dx"] = xs
    source_params[ii]["dz"] = zs
    source_params[ii]["dx'"] = xps
    source_params[ii]["dz'"] = zps

    fig.add_trace(go.Line(x=energy, y=flux, name=f"K = {uconf["K"]}, h{uconf["harmonic"]}"))
fig.show()

source_params = pd.DataFrame(source_params)
source_params = source_params.set_index("E")
source_params.to_csv("Undulator_1-1_params.csv")
print(source_params)

OpenCL: bulding undulator.cl ...
OpenCL: found 1 CPU
OpenCL: found 1 GPU
OpenCL: found none other accelerator
OpenCL for undulator.cl: Autoselected device 0: 12th Gen Intel(R) Core(TM) i7-12800HX
precisionOpenCL = float64


/nix/store/wi0gs2lg75vbsz87x8ynaaalmkhxj1mw-python3.12-pyopencl-2025.1/lib/python3.12/site-packages/pyopencl/cache.py:496: CompilerWarning:

Built kernel retrieved from cache. Original from-source build had warnings:
Build on <pyopencl.Device '12th Gen Intel(R) Core(TM) i7-12800HX' on 'Intel(R) OpenCL' at 0x41e37038> succeeded, but said:

Compilation started
Compilation done
Linking started
Linking done
Device build started
Device build done
Kernel <undulator> was successfully vectorized (8)
Kernel <undulator_taper> was successfully vectorized (8)
Kernel <undulator_nf> was successfully vectorized (8)
Kernel <undulator_full> was successfully vectorized (8)
Kernel <undulator_nf_full> was successfully vectorized (8)
Kernel <get_trajectory_filament> was successfully vectorized (8)
Kernel <custom_field_filament> was successfully vectorized (8)
Kernel <get_trajectory> was successfully vectorized (8)
Kernel <custom_field> was successfully vectorized (8)
Done.

/nix/store/wi0gs2lg75vbsz87x8yna

Estimating convergence
Phase 1. Exponential / rough
Phase 2. Bisection / precize. 0 steps
Done estimating convergence
Done with integration optimization, 32 points will be used in 2 intervals


/nix/store/i63lpv0lgmz4gmar81x5rxksyc2nm66f-python3.12-plotly-5.24.1/lib/python3.12/site-packages/plotly/graph_objs/_deprecations.py:378: DeprecationWarning:

plotly.graph_objs.Line is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.scatter.Line
  - plotly.graph_objs.layout.shape.Line
  - etc.




OpenCL: bulding undulator.cl ...
OpenCL: found 1 CPU
OpenCL: found 1 GPU
OpenCL: found none other accelerator
OpenCL for undulator.cl: Autoselected device 0: 12th Gen Intel(R) Core(TM) i7-12800HX
precisionOpenCL = float64
Estimating convergence
Phase 1. Exponential / rough
Phase 2. Bisection / precize. 0 steps
Done estimating convergence
Done with integration optimization, 32 points will be used in 2 intervals
OpenCL: bulding undulator.cl ...
OpenCL: found 1 CPU
OpenCL: found 1 GPU
OpenCL: found none other accelerator
OpenCL for undulator.cl: Autoselected device 0: 12th Gen Intel(R) Core(TM) i7-12800HX
precisionOpenCL = float64
Estimating convergence
Phase 1. Exponential / rough
Phase 2. Bisection / precize. 0 steps
Done estimating convergence
Done with integration optimization, 32 points will be used in 2 intervals


           K  harmonic      E FWHM        dx        dz       dx'       dz'
E                                                                         
8800   1.309         3  162.247860  0.038931  0.006036  0.000007  0.000007
15000  1.760         7  176.396078  0.038888  0.005750  0.000010  0.000010
17000  1.580         7  218.511848  0.038871  0.005635  0.000010  0.000009
